In [65]:
import sys
#!{sys.executable} -m pip install git+https://github.com/Corollarium/geograpy
!{sys.executable} -m pip install textblob

    100% |████████████████████████████████| 645kB 3.8MB/s ta 0:00:01
You are using pip version 18.1, however version 20.0.2 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [66]:
import os
import re
import json
import nltk
import certifi
import ssl
import time
import requests
import pycountry

import numpy as np
import pandas as pd
import country_converter as coco
from countryinfo import CountryInfo
from textblob import TextBlob
from textblob.sentiments import NaiveBayesAnalyzer

import tika.tika
from tika import parser

In [2]:
df = pd.read_parquet('../documents_processed.parquet')

In [3]:
df.head()

abstract  \
0  Bordetella bronchiseptica isolate KM22 has bee...   
1                                                      
2  The influenza A nucleoprotein (NP) is an attra...   
3  The outbreak of severe acute respiratory syndr...   
4  The prevalence of feline herpesvirus-1 (FHV-1)...   

                                           body_text  \
0  20-kb insert library preparation protocol (htt...   
1  I nfectious diseases have been an ever-present...   
2  The transmission of a pathogenic avian H5N1 vi...   
3  acute lung injury; inflammatory response; neut...   
4  Feline herpesvirus type 1 (FHV-1) is the most ...   

                                        sha  \
0  8f8eb4f004c2002face0723f2f58cc411954d36e   
1  63f7049d200896290b38b38711113054f7ea1b50   
2  4df45b8404d9de0b376a8ae3c282a517df36fe51   
3  e0737ee93afe7b0bf06b1e3f9adf21d541dd10f0   
4  3c3572ba243d61e7631725669c8f88347fdbd5bc   

                                         doi_x  \
0       http://dx.doi.org/10.1128/MRA.01207-19   
1     http://dx.doi.org/10.3201/eid1104.041167   
2     http://dx.doi.org/10.1051/vetres/2009071   
3  http://dx.doi.org/10.1038/labinvest.2012.92   
4   http://dx.doi.org/10.4142/jvs.2008.9.2.207   

                                         doi_y source_x  \
0       http://dx.doi.org/10.1128/MRA.01207-19      PMC   
1     http://dx.doi.org/10.3201/eid1104.041167      PMC   
2     http://dx.doi.org/10.1051/vetres/2009071      PMC   
3  http://dx.doi.org/10.1038/labinvest.2012.92      PMC   
4   http://dx.doi.org/10.4142/jvs.2008.9.2.207      PMC   

                    journal  has_full_text  
0  Microbiol Resour Announc           True  
1          Emerg Infect Dis           True  
2                   Vet Res           True  
3                Lab Invest           True  
4                 J Vet Sci           True

In [ ]:
os.mkdir("raw_body_text")

In [ ]:
os.mkdir("geotopic_output")

In [ ]:
for p in df.index:
    f = open("raw_body_text/" + df['sha'][p] + ".geot", "a")
    f.write(df['body_text'][p])
    f.close()

In [ ]:
home = os.getenv('HOME')

In [ ]:
tika.tika.TikaServerClasspath = '/Users/anastasia/geotopicparser-utils/mime:/Users/anastasia/geotopicparser-utils/models/polar:/Users/anastasia/geotopic-mime/tika-config.xml'
parsed = parser.from_file(home + '/geotopicparser-utils/geotopics/polar.geot')
#if 'org.apache.tika.parser.csv.TextAndCSVParser' in parsed["metadata"]['X-Parsed-By']:
print(parsed["metadata"])

In [ ]:
tika.tika.TikaServerClasspath = home + '/geotopicparser-utils/mime:'+home+'/geotopicparser-utils/models/polar'
for file in os.listdir("./raw_body_text"):
    parsed = parser.from_file("./raw_body_text/" + file)
    if 'org.apache.tika.parser.geo.topic.GeoParser' not in parsed["metadata"]['X-Parsed-By']:
        continue
    print("YES")
    json_object = json.dumps(parsed["metadata"], indent = 4) 
    with open("geotopic_output/" + os.path.basename(file).split('.')[0] + ".json", "w") as outfile: 
        outfile.write(json_object) 

In [ ]:
# Another method through the terminal:

! java -classpath tika-app-1.24.jar:$HOME/src/location-ner-model:$HOME/src/geotopic-mime org.apache.tika.cli.TikaCLI -m /Users/anastasia/Desktop/JPL_Remote/covid_19/github_repo/bert_experiments/raw_body_text/0a00a6df208e068e7aa369fb94641434ea0e6070.geot

# ===============================================================

# GeoText

In [6]:
def correct_locations(locations):
    correct_locations = []
    for city in locations:
        correct = True
        tagged = nltk.pos_tag(nltk.word_tokenize(city))
        for tup in tagged:
            if tup[1] != 'NNP' and tup[1] != 'NNPS':
                correct = False
                break
        if correct:
            correct_locations.append(city)
    return correct_locations

In [7]:
def multiple_mentions(data):
    new_geodata = {}
    for paper in data:
        new_geodata[paper] = {}
        for loc in data[paper]:
            seen = set()
            unique = {}
            for place in data[paper][loc]:
                if place not in seen:
                    unique[place] = 1
                    seen.add(place)
                else:
                    unique[place] += 1
            new_geodata[paper][loc] = unique
    return new_geodata

In [8]:
from geopy import geocoders 
import geopy.geocoders
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter

def get_lat_lon(data):
    ctx = ssl.create_default_context(cafile=certifi.where())
    geopy.geocoders.options.default_ssl_context = ctx
    gn = geocoders.GeoNames(username="anastasija")
    geolocator = Nominatim(user_agent="anastasija", timeout=10, scheme='http')
    geoc = RateLimiter(geolocator.geocode, min_delay_seconds=2)
    for paper in data:
        for loc in data[paper]:
            for place in data[paper][loc]:
                count = data[paper][loc][place]
                data[paper][loc][place] = {}
                try:
                    location = geolocator.geocode(place)
                    data[paper][loc][place]['lat'] = location.latitude
                    data[paper][loc][place]['lon'] = location.longitude
                except:
                    pass
                data[paper][loc][place]['mentioned'] = count
                time.sleep(0.5)
    return data

In [9]:
from geotext import GeoText

geodata = {}
for file in os.listdir("./raw_body_text"):
    with open("./raw_body_text/" + file, 'r') as f:
        text = f.read()
    places = GeoText(text)
    sha = os.path.basename(file).split('.')[0]
    geodata[sha] = {}
    geodata[sha]["countries"] = correct_locations(places.countries)
    geodata[sha]["cities"] = correct_locations(places.cities)

In [10]:
geodata_final = get_lat_lon(multiple_mentions(geodata))

In [11]:
with open('./geodata/geo.json', 'w') as fp:
    json.dump(geodata_final, fp, indent=4)

In [145]:
geodata_final

{'fd31ade73c720f893a5ddb2370df90a84511ec4a': {'countries': {'Brazil': {'lat': -10.3333333,
    'lon': -53.2,
    'mentioned': 14},
   'United States': {'lat': 39.7837304, 'lon': -100.4458825, 'mentioned': 1},
   'Germany': {'lat': 51.0834196, 'lon': 10.4234469, 'mentioned': 1},
   'Italy': {'lat': 42.6384261, 'lon': 12.674297, 'mentioned': 1},
   'Spain': {'lat': 39.3262345, 'lon': -4.8380649, 'mentioned': 1},
   'Taiwan': {'lat': 23.9739374, 'lon': 120.9820179, 'mentioned': 1}},
  'cities': {'Belo Horizonte': {'lat': -19.9227318,
    'lon': -43.9450948,
    'mentioned': 1},
   'Iowa': {'lat': 41.9216734, 'lon': -93.3122705, 'mentioned': 1},
   'São Paulo': {'lat': -23.5506507, 'lon': -46.6333824, 'mentioned': 1}}},
 '0b65341c3090421acaac37ec4c93212277be55bb': {'countries': {}, 'cities': {}}}

# =============================================================

# Temperatures

https://openweathermap.org/guide

In [20]:
def weather_data(place, api):
    # TODO: add try, except
    try:
        res = requests.get('http://api.openweathermap.org/data/2.5/weather?q=' + place + '&APPID=' + api + '&units=metric')
        return res.json()
    except:
        pass

In [5]:
api_key = '41b313deb9181d0ed9bb57021f2ebe68'

In [28]:
geodata = {}
with open('geo.json') as f:
    geodata = json.load(f)

In [29]:
geodata

{'fd31ade73c720f893a5ddb2370df90a84511ec4a': {'countries': {'Brazil': {'lat': -10.3333333,
    'lon': -53.2,
    'mentioned': 14},
   'United States': {'lat': 39.7837304, 'lon': -100.4458825, 'mentioned': 1},
   'Germany': {'lat': 51.0834196, 'lon': 10.4234469, 'mentioned': 1},
   'Italy': {'lat': 42.6384261, 'lon': 12.674297, 'mentioned': 1},
   'Spain': {'lat': 39.3262345, 'lon': -4.8380649, 'mentioned': 1},
   'Taiwan': {'lat': 23.9739374, 'lon': 120.9820179, 'mentioned': 1}},
  'cities': {'Belo Horizonte': {'lat': -19.9227318,
    'lon': -43.9450948,
    'mentioned': 1},
   'Iowa': {'lat': 41.9216734, 'lon': -93.3122705, 'mentioned': 1},
   'São Paulo': {'lat': -23.5506507, 'lon': -46.6333824, 'mentioned': 1}}},
 '0b65341c3090421acaac37ec4c93212277be55bb': {'countries': {}, 'cities': {}},
 'd6f350fa81730f8476614ffe7280454633d77f31': {'countries': {'Japan': {'lat': 36.5748441,
    'lon': 139.2394179,
    'mentioned': 1},
   'Hungary': {'lat': 47.1817585, 'lon': 19.5060937, 'mentione

In [8]:
def get_unique_places(data):
    countries = []
    cities = []
    all_places = []
    for paper in data:
        for loc in data[paper]:
            if data[paper][loc]:
                for pl in data[paper][loc]:
                    all_places.append(pl)
                    if loc == 'countries':
                        countries.append(pl)
                    elif loc == 'cities':
                        cities.append(pl)
    unique_countries = set(countries)
    unique_cities = set(cities)
    unique_places = set(all_places)
    return (all_places, unique_countries, unique_cities)

In [9]:
(unique_places, unique_countries, unique_cities) = get_unique_places(geodata)

In [10]:
unique_places

['Brazil',
 'United States',
 'Germany',
 'Italy',
 'Spain',
 'Taiwan',
 'Belo Horizonte',
 'Iowa',
 'São Paulo',
 'Japan',
 'Hungary',
 'Taiwan',
 'China',
 'Vietnam',
 'Cambodia',
 'Bangladesh',
 'Ghana',
 'China',
 'March',
 'China',
 'Mitchell',
 'Hong Kong',
 'China',
 'University',
 'Tai Po',
 'March',
 'Brazil',
 'Australia',
 'Grand Island',
 'Billerica',
 'Saudi Arabia',
 'South Korea',
 'China',
 'University',
 'Beijing',
 'San Francisco',
 'San Diego',
 'Waltham',
 'Foster City',
 'Hong Kong',
 'United Kingdom',
 'Switzerland',
 'Wilmington',
 'Coralville',
 'San Diego',
 'March',
 'University',
 'Santa Cruz',
 'Australia',
 'Germany',
 'Switzerland',
 'Italy',
 'Vienna',
 'Vietnam',
 'China',
 'Japan',
 'United States',
 'Kakuda',
 'Atlanta',
 'University',
 'Konstanz',
 'New Zealand',
 'United States',
 'Atlanta',
 'Japan',
 'Canada',
 'China',
 'Beijing',
 'Australia',
 'United States',
 'Puerto Rico',
 'Angola',
 'Germany',
 'Switzerland',
 'Florida',
 'Rockville',
 'Gee

In [48]:
def get_current_weather(countries, cities):
    curr_temp = {}
    for city in cities:
        curr_temp[city.title()] = weather_data(city, api_key)
        time.sleep(1)
    new_countries = []
    for country in countries:
        formatted_name = country.title()
        new_countries.append(formatted_name)
    codes = coco.convert(names=new_countries, to='ISO2')
    # Weather doesn't work for countries so I will be using capital cities of each country
    for code, country in zip(codes, new_countries):
        if country == 'Gambia':
            country = 'The Gambia'
        c = CountryInfo(country)
        try:
            curr_temp[country.title()] = weather_data(c.capital(), api_key)
        except:
            pass
        time.sleep(1)
    return curr_temp

In [39]:
curr_temp = get_current_weather(unique_countries, unique_cities)

In [42]:
curr_temp

{'El Paso': {'coord': {'lon': -106.49, 'lat': 31.76},
  'weather': [{'id': 803,
    'main': 'Clouds',
    'description': 'broken clouds',
    'icon': '04n'}],
  'base': 'stations',
  'main': {'temp': 14.28,
   'feels_like': 9.96,
   'temp_min': 12.78,
   'temp_max': 16.11,
   'pressure': 1015,
   'humidity': 28},
  'visibility': 16093,
  'wind': {'speed': 2.6, 'deg': 80},
  'clouds': {'all': 75},
  'dt': 1585552035,
  'sys': {'type': 1,
   'id': 3974,
   'country': 'US',
   'sunrise': 1585572965,
   'sunset': 1585617844},
  'timezone': -21600,
  'id': 5520993,
  'name': 'El Paso',
  'cod': 200},
 'Berkeley': {'coord': {'lon': -122.27, 'lat': 37.87},
  'weather': [{'id': 801,
    'main': 'Clouds',
    'description': 'few clouds',
    'icon': '02n'}],
  'base': 'stations',
  'main': {'temp': 10.27,
   'feels_like': 8.38,
   'temp_min': 8.33,
   'temp_max': 12.22,
   'pressure': 1022,
   'humidity': 87},
  'visibility': 16093,
  'wind': {'speed': 2.1, 'deg': 140},
  'clouds': {'all': 20},

In [61]:
len(curr_temp)

836

In [62]:
geodata_new = geodata
for paper in geodata_new:
    for loc in geodata_new[paper]:
        for pl in geodata_new[paper][loc]:
            if pl == 'Gambia':
                geodata_new[paper][loc][pl.title()]['weather'] = curr_temp['The Gambia']
            elif pl == 'Antarctica':
                continue
            elif pl == 'VietNam':
                pl = 'Vietnam'
            else:
                try:
                    geodata_new[paper][loc][pl]['weather'] = curr_temp[pl]
                except:
                    geodata_new[paper][loc][pl]['weather'] = {}

In [63]:
geodata_new

{'fd31ade73c720f893a5ddb2370df90a84511ec4a': {'countries': {'Brazil': {'lat': -10.3333333,
    'lon': -53.2,
    'mentioned': 14,
    'weather': {'coord': {'lon': -47.93, 'lat': -15.78},
     'weather': [{'id': 803,
       'main': 'Clouds',
       'description': 'broken clouds',
       'icon': '04n'}],
     'base': 'stations',
     'main': {'temp': 17.11,
      'feels_like': 18.03,
      'temp_min': 16.11,
      'temp_max': 18,
      'pressure': 1019,
      'humidity': 93},
     'visibility': 10000,
     'wind': {'speed': 1.5, 'deg': 260},
     'clouds': {'all': 82},
     'dt': 1585552901,
     'sys': {'type': 1,
      'id': 8336,
      'country': 'BR',
      'sunrise': 1585559817,
      'sunset': 1585602889},
     'timezone': -10800,
     'id': 3469058,
     'name': 'Brasília',
     'cod': 200}},
   'United States': {'lat': 39.7837304,
    'lon': -100.4458825,
    'mentioned': 1,
    'weather': {'coord': {'lon': -77.04, 'lat': 38.9},
     'weather': [{'id': 741,
       'main': 'Fog',


In [64]:
with open('./geodata/geo_weather.json', 'w') as fp:
    json.dump(geodata_new, fp, indent=4)

# ============================================================

# Sentiment Analysis on Main Paper Body

In [75]:
blob = TextBlob((re.sub('[^A-z0-9 -]', ' ', df.loc[100]['body_text'])), analyzer=NaiveBayesAnalyzer())
blob.sentiment

Sentiment(classification='pos', p_pos=1.0, p_neg=2.3319523497078063e-69)